## Imports

In [1]:
import pandas as pd
import numpy as np

pd.options.display.max_rows = 5000
pd.options.display.max_seq_items = 2000

## Reading in the datasets

#### Faults dataset

In [2]:
faults = pd.read_csv('../data/J1939Faults.csv',
                     low_memory=False, 
                     parse_dates=[2, 19],
                     infer_datetime_format=True)

In [3]:
faults.head()

RecordID  ESS_Id      EventTimeStamp  \
0         1  990349 2015-02-21 10:47:13   
1         2  990360 2015-02-21 11:34:34   
2         3  990364 2015-02-21 11:35:31   
3         4  990370 2015-02-21 11:35:33   
4         5  990416 2015-02-21 11:39:41   

                          eventDescription  actionDescription  \
0  Low (Severity Low) Engine Coolant Level                NaN   
1                                      NaN                NaN   
2      Incorrect Data Steering Wheel Angle                NaN   
3      Incorrect Data Steering Wheel Angle                NaN   
4                                      NaN                NaN   

                     ecuSoftwareVersion ecuSerialNumber              ecuModel  \
0                               unknown         unknown               unknown   
1                               unknown         unknown               unknown   
2                               unknown         unknown               unknown   
3                               unknown         unknown               unknown   
4  22281684P01*22357957P01*22362082P01*        13063430  0USA13_13_0415_2238A   

   ecuMake  ecuSource   spn  fmi  active  activeTransitionCount  faultValue  \
0  unknown          0   111   17    True                      2         NaN   
1  unknown         11   629   12    True                    127         NaN   
2  unknown         11  1807    2   False                    127         NaN   
3  unknown         11  1807    2    True                    127         NaN   
4    VOLVO          0  4364   17   False                      2         NaN   

  EquipmentID  MCTNumber   Latitude  Longitude   LocationTimeStamp  
0        1439  105354361  38.857638 -84.626851 2015-02-21 11:34:25  
1        1439  105354361  38.857638 -84.626851 2015-02-21 11:35:10  
2        1369  105336226  41.421250 -87.767361 2015-02-21 11:35:26  
3        1369  105336226  41.421018 -87.767361 2015-02-21 11:36:08  
4        1674  105427130  38.416481 -89.442638 2015-02-21 11:39:37

#### Diagnostics dataset

In [4]:
diagnostic = pd.read_csv('../data/VehicleDiagnosticOnboardData.csv')

In [5]:
diagnostic.head()

Id                  Name     Value  FaultId
0   1             IgnStatus     False        1
1   2     EngineOilPressure         0        1
2   3  EngineOilTemperature  96.74375        1
3   4    TurboBoostPressure         0        1
4   5            EngineLoad        11        1

This data needs to be flattened. We'll use a pivot so it will be ready to join to the Faults data

In [6]:
diagnostic = diagnostic.pivot(index='FaultId', columns='Name', values='Value').reset_index()

In [7]:
diagnostic.head()

Name  FaultId AcceleratorPedal BarometricPressure CruiseControlActive  \
0           1                0              14.21               False   
1           2              NaN                NaN                 NaN   
2           3              NaN                NaN                 NaN   
3           4              NaN                NaN                 NaN   
4           5              NaN                NaN                 NaN   

Name CruiseControlSetSpeed DistanceLtd EngineCoolantTemperature EngineLoad  \
0                 66.48672    423178.7                    100.4         11   
1                      NaN         NaN                      NaN        NaN   
2                      NaN         NaN                      NaN        NaN   
3                      NaN         NaN                      NaN        NaN   
4                      NaN         NaN                      NaN        NaN   

Name EngineOilPressure EngineOilTemperature  ... FuelTemperature IgnStatus  \
0                    0             96.74375  ...             NaN     False   
1                  NaN                  NaN  ...             NaN      True   
2                  NaN                  NaN  ...             NaN       NaN   
3                  NaN                  NaN  ...             NaN      True   
4                  NaN                  NaN  ...             NaN       NaN   

Name IntakeManifoldTemperature LampStatus ParkingBrake ServiceDistance Speed  \
0                         78.8       1023         True             NaN     0   
1                          NaN       1279          NaN             NaN   NaN   
2                          NaN       1279          NaN             NaN   NaN   
3                          NaN       1279          NaN             NaN   NaN   
4                          NaN      16639          NaN             NaN   NaN   

Name SwitchedBatteryVoltage Throttle TurboBoostPressure  
0                   3276.75      NaN                  0  
1                       NaN      NaN                NaN  
2                       NaN      NaN                NaN  
3                       NaN      NaN                NaN  
4                       NaN      NaN                NaN  

[5 rows x 25 columns]

## Joining the two datasets

In [8]:
faults_diagnostic = faults.merge(diagnostic, left_on='RecordID', right_on='FaultId')

In [9]:
faults_diagnostic.head()

RecordID  ESS_Id      EventTimeStamp  \
0         1  990349 2015-02-21 10:47:13   
1         2  990360 2015-02-21 11:34:34   
2         3  990364 2015-02-21 11:35:31   
3         4  990370 2015-02-21 11:35:33   
4         5  990416 2015-02-21 11:39:41   

                          eventDescription  actionDescription  \
0  Low (Severity Low) Engine Coolant Level                NaN   
1                                      NaN                NaN   
2      Incorrect Data Steering Wheel Angle                NaN   
3      Incorrect Data Steering Wheel Angle                NaN   
4                                      NaN                NaN   

                     ecuSoftwareVersion ecuSerialNumber              ecuModel  \
0                               unknown         unknown               unknown   
1                               unknown         unknown               unknown   
2                               unknown         unknown               unknown   
3                               unknown         unknown               unknown   
4  22281684P01*22357957P01*22362082P01*        13063430  0USA13_13_0415_2238A   

   ecuMake  ecuSource  ...  FuelTemperature  IgnStatus  \
0  unknown          0  ...              NaN      False   
1  unknown         11  ...              NaN       True   
2  unknown         11  ...              NaN        NaN   
3  unknown         11  ...              NaN       True   
4    VOLVO          0  ...              NaN        NaN   

   IntakeManifoldTemperature  LampStatus  ParkingBrake ServiceDistance  Speed  \
0                       78.8        1023          True             NaN      0   
1                        NaN        1279           NaN             NaN    NaN   
2                        NaN        1279           NaN             NaN    NaN   
3                        NaN        1279           NaN             NaN    NaN   
4                        NaN       16639           NaN             NaN    NaN   

   SwitchedBatteryVoltage  Throttle TurboBoostPressure  
0                 3276.75       NaN                  0  
1                     NaN       NaN                NaN  
2                     NaN       NaN                NaN  
3                     NaN       NaN                NaN  
4                     NaN       NaN                NaN  

[5 rows x 45 columns]

## Cleaning

#### Column names

In [10]:
#My team opted to use snake case for column names

faults_diagnostic = faults_diagnostic.rename(columns={
    "RecordID": "record_id",
    "ESS_Id": "ess_id",
    "EventTimeStamp": "event_timestamp",
    "eventDescription": "event_description",
    "actionDescription": "action_description",
    "ecuSoftwareVersion": "ecu_software_version",
    "ecuSerialNumber": "ecu_serial_number",
    "ecuModel": "ecu_model",
    "ecuMake": "ecu_make",
    "ecuSource": "ecu_source",
    "activeTransitionCount": "active_transition_count",
    "faultValue": "fault_value",
    "EquipmentID": "equipment_id",
    "MCTNumber": "mct_number",
    "Latitude": "latitude",
    "Longitude": "longitude",
    "LocationTimeStamp": "location_timestamp",
    "FaultId": "fault_id",
    "AcceleratorPedal": "accelerator_pedal",
    "BarometricPressure": "barometric_pressure",
    "CruiseControlActive": "cruise_control_active",
    "CruiseControlSetSpeed": "cruise_control_set_speed",
    "DistanceLtd": "distance_ltd",
    "EngineCoolantTemperature": "engine_coolant_temperature",
    "EngineLoad": "engine_load",
    "EngineOilPressure": "engine_oil_pressure",
    "EngineOilTemperature": "engine_oil_temperature",
    "EngineRpm": "engine_rpm",
    "EngineTimeLtd": "engine_time_ltd",
    "FuelLevel": "fuel_level",
    "FuelLtd": "fuel_ltd",
    "FuelRate": "fuel_rate",
    "FuelTemperature": "fuel_temperature",
    "IgnStatus": "ign_status",
    "IntakeManifoldTemperature": "intake_manifold_temperature",
    "LampStatus": "lamp_status",
    "ParkingBrake": "parking_brake",
    "ServiceDistance": "service_distance",
    "Speed": "speed",
    "SwitchedBatteryVoltage": "switched_battery_voltage",
    "Throttle": "throttle",
    "TurboBoostPressure": "turbo_boost_pressure"
})

In [11]:
# The columns 'action_description' and 'fault_value' contain all null values, so they will be dropped

faults_diagnostic = faults_diagnostic.drop(columns=['action_description', 'fault_value'])

In [12]:
faults_diagnostic.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 1187335 entries, 0 to 1187334
Data columns (total 43 columns):
 #   Column                       Non-Null Count    Dtype         
---  ------                       --------------    -----         
 0   record_id                    1187335 non-null  int64         
 1   ess_id                       1187335 non-null  int64         
 2   event_timestamp              1187335 non-null  datetime64[ns]
 3   event_description            1126490 non-null  object        
 4   ecu_software_version         891285 non-null   object        
 5   ecu_serial_number            844318 non-null   object        
 6   ecu_model                    1122577 non-null  object        
 7   ecu_make                     1122577 non-null  object        
 8   ecu_source                   1187335 non-null  int64         
 9   spn                          1187335 non-null  int64         
 10  fmi                          1187335 non-null  int64         
 11  active     

#### Column data types

In [13]:
faults_diagnostic.head()

record_id  ess_id     event_timestamp  \
0          1  990349 2015-02-21 10:47:13   
1          2  990360 2015-02-21 11:34:34   
2          3  990364 2015-02-21 11:35:31   
3          4  990370 2015-02-21 11:35:33   
4          5  990416 2015-02-21 11:39:41   

                         event_description  \
0  Low (Severity Low) Engine Coolant Level   
1                                      NaN   
2      Incorrect Data Steering Wheel Angle   
3      Incorrect Data Steering Wheel Angle   
4                                      NaN   

                   ecu_software_version ecu_serial_number  \
0                               unknown           unknown   
1                               unknown           unknown   
2                               unknown           unknown   
3                               unknown           unknown   
4  22281684P01*22357957P01*22362082P01*          13063430   

              ecu_model ecu_make  ecu_source   spn  ...  fuel_temperature  \
0               unknown  unknown           0   111  ...               NaN   
1               unknown  unknown          11   629  ...               NaN   
2               unknown  unknown          11  1807  ...               NaN   
3               unknown  unknown          11  1807  ...               NaN   
4  0USA13_13_0415_2238A    VOLVO           0  4364  ...               NaN   

   ign_status  intake_manifold_temperature lamp_status  parking_brake  \
0       False                         78.8        1023           True   
1        True                          NaN        1279            NaN   
2         NaN                          NaN        1279            NaN   
3        True                          NaN        1279            NaN   
4         NaN                          NaN       16639            NaN   

   service_distance  speed switched_battery_voltage  throttle  \
0               NaN      0                  3276.75       NaN   
1               NaN    NaN                      NaN       NaN   
2               NaN    NaN                      NaN       NaN   
3               NaN    NaN                      NaN       NaN   
4               NaN    NaN                      NaN       NaN   

  turbo_boost_pressure  
0                    0  
1                  NaN  
2                  NaN  
3                  NaN  
4                  NaN  

[5 rows x 43 columns]

##### Software Versions

In [14]:
faults_diagnostic[faults_diagnostic['ecu_software_version'].str.contains("?", regex=False, na=False)]

record_id     ess_id     event_timestamp  \
20828        21711    1878624 2015-04-14 11:38:36   
20829        21712    1878625 2015-04-14 11:38:36   
23937        24820    1933193 2015-04-16 19:49:37   
23938        24821    1933194 2015-04-16 19:49:37   
40226        41338    2216854 2015-05-02 14:45:37   
40483        41595    2221486 2015-05-03 09:47:01   
81635        84021    2897660 2015-06-11 07:43:50   
90267        92653    3037645 2015-06-19 06:36:05   
90273        92659    3037705 2015-06-19 06:39:59   
91224        93610    3054166 2015-06-20 01:31:30   
91225        93611    3054179 2015-06-20 01:35:27   
121168      123554    3486482 2015-07-15 13:07:37   
121169      123555    3486493 2015-07-15 13:09:00   
137680      140066    3711771 2015-07-28 04:18:49   
173884      176270    4187612 2015-08-21 10:10:08   
192595      194981    4478021 2015-09-07 04:44:26   
201513      203899    4623295 2015-09-15 07:14:16   
201524      203910    4623396 2015-09-15 07:19:39   
250601      254421    5387234 2015-10-25 04:06:16   
251399      255219    5398340 2015-10-26 06:46:47   
267782      271602    5672679 2015-11-09 13:11:23   
267952      271772    5675840 2015-11-09 15:52:09   
268309      272129    5682031 2015-11-10 03:31:51   
270096      273916    5712857 2015-11-11 10:12:37   
270151      273971    5713816 2015-11-11 10:49:52   
283343      287849    5928171 2015-11-22 11:41:26   
283585      288091    5931105 2015-11-22 15:33:52   
299026      303532    6181884 2015-12-07 13:50:27   
299037      303543    6182259 2015-12-07 14:05:27   
304595      309101    6282207 2015-12-12 02:17:38   
310935      315992    6387858 2015-12-17 14:07:08   
334621      339678    6754717 2016-01-09 09:02:14   
334644      339701    6754906 2016-01-09 09:03:05   
378932      386433    7499008 2016-02-17 03:25:36   
385847      393348    7614898 2016-02-23 07:07:42   
420948      429215    8262650 2016-03-28 00:03:54   
420949      429216    8262652 2016-03-28 00:05:16   
435605      443872    8549139 2016-04-11 13:38:00   
435606      443873    8549140 2016-04-11 13:38:00   
457193      466310    8976744 2016-05-03 10:38:23   
457305      466422    8979081 2016-05-03 12:10:47   
457317      466434    8979405 2016-05-03 12:23:37   
457353      466470    8980137 2016-05-03 12:50:12   
457355      466472    8980162 2016-05-03 12:52:09   
457434      466551    8981857 2016-05-03 13:54:57   
457443      466560    8981933 2016-05-03 13:58:44   
457489      466606    8982910 2016-05-03 14:36:33   
457528      466645    8983623 2016-05-03 15:08:53   
457541      466658    8983853 2016-05-03 15:12:06   
470336      479453    9270382 2016-05-18 14:05:48   
472602      481719    9320260 2016-05-20 18:02:08   
475947      485064    9396390 2016-05-25 09:46:31   
475951      485068    9396398 2016-05-25 09:45:52   
475952      485069    9396399 2016-05-25 09:45:52   
475953      485070    9396404 2016-05-25 09:46:01   
475959      485076    9396500 2016-05-25 09:49:43   
475960      485077    9396501 2016-05-25 09:49:43   
475961      485078    9396502 2016-05-25 09:49:43   
478982      488099    9471204 2016-05-29 07:28:46   
478987      488104    9471209 2016-05-29 07:28:08   
478988      488105    9471210 2016-05-29 07:28:08   
478989      488106    9471212 2016-05-29 07:28:16   
478991      488108    9471250 2016-05-29 07:33:53   
478992      488109    9471251 2016-05-29 07:33:53   
478993      488110    9471252 2016-05-29 07:33:53   
485170      494287    9605167 2016-06-06 07:31:59   
485172      494289    9605169 2016-06-06 07:31:59   
485189      494306    9605449 2016-06-06 07:47:26   
485197      494314    9605498 2016-06-06 07:50:35   
524673      536550   10499304 2016-07-21 09:11:48   
524680      536557   10499374 2016-07-21 09:15:20   
524682      536559   10499377 2016-07-21 09:15:21   
524696      536573   10499556 2016-07-21 09:18:36   
530547      542424   10630152 2016-07-27 19:45:40   
530548      542425   10630161 2016

##### Engine Serial Number

In [15]:
faults_diagnostic['ecu_serial_number'].value_counts()

unknown            298549
6U13D13             11207
79845785            10302
79856768             8158
79845329             7199
79623056             7066
79621048             6828
79845786             6349
79840984             6345
79844876             5872
79623054             5663
79623410             5578
79844877             5506
79620769             5482
79844882             5417
79614871             5326
79615187             5218
79857688             5059
79857689             5019
79614865             4374
79619434             4206
79620768             4133
79615184             3857
79845331             3819
79619117             3797
79614866             3788
S381222841           3176
79615183             3169
79845327             3149
79844880             3113
79857687             3089
79857685             3065
00000000             3062
79620774             3055
79618850             3041
79619125             2855
79607068             2798
79620764             2798
79623055    

There are 'unknown' (298549), 'Unspecified' (97), and NoSerial (3) values. Let's combine them all into 'unknown'

In [16]:
faults_diagnostic['ecu_serial_number'] = faults_diagnostic['ecu_serial_number'].replace('Unspecified', 'unknown')
faults_diagnostic['ecu_serial_number'] = faults_diagnostic['ecu_serial_number'].replace('NoSerial', 'unknown')

##### Engine Model

In [17]:
faults_diagnostic['ecu_model'].sort_values().unique()

array(['0USA10_13_0405_2237A', '0USA13_13_0415_2238A', '202.35.0',
       '20412511P07', '6L u13D0890000000', '6U13D13', '6X1u10D1500000000',
       '6X1u13D1500000000', '6X1u17D1500000000', '6X1u20D1500000000',
       'CE', 'CECU3-NAMUX3', 'CECU3B-NAMUX4', 'E0031', 'EC60-adv',
       'EC80ESP', 'EC80ESP AM000036', 'EC80ESP AM000038', 'EC80ESP+',
       'EEO-xxF112C', 'FAOM-xx810S-EC3', 'Gen 4 Boot Loader', 'MX',
       'MX16U13D13', 'MX16U15D13', 'Y044053', 'Y049568',
       '________Y043718', 'unknown', nan], dtype=object)

Nothing to update for models

##### Engine Make

In [18]:
faults_diagnostic['ecu_make'].value_counts()

CMMNS              433403
unknown            298549
PACCR              277021
BNDWS               71001
PCAR                20229
EATON               12612
VOLVO                7252
?????                 755
????S                 627
????R                 589
?MMNS                 289
?CAR                  152
?ACCR                  39
???CR                  20
?NDWS                  15
?????MX16U13D13         9
?????MX                 6
?ATON                   3
??MNS                   3
5516014                 1
???R                    1
??DWS                   1
Name: ecu_make, dtype: int64

In [19]:
faults_diagnostic['ecu_make'] = faults_diagnostic['ecu_make'].replace('?????', 'unknown')
faults_diagnostic['ecu_make'] = faults_diagnostic['ecu_make'].replace('????R', 'PACCR')
faults_diagnostic['ecu_make'] = faults_diagnostic['ecu_make'].replace('?MMNS', 'CMMNS')
faults_diagnostic['ecu_make'] = faults_diagnostic['ecu_make'].replace('?CAR', 'PCAR')
faults_diagnostic['ecu_make'] = faults_diagnostic['ecu_make'].replace('?ACCR', 'PACCR')
faults_diagnostic['ecu_make'] = faults_diagnostic['ecu_make'].replace('???CR', 'PACCR')
faults_diagnostic['ecu_make'] = faults_diagnostic['ecu_make'].replace('?NDWS', 'BNDWS')
faults_diagnostic['ecu_make'] = faults_diagnostic['ecu_make'].replace('?????MX16U13D13', 'MX16U13D13')
faults_diagnostic['ecu_make'] = faults_diagnostic['ecu_make'].replace('?????MX', 'MX')
faults_diagnostic['ecu_make'] = faults_diagnostic['ecu_make'].replace('?ATON', 'EATON')
faults_diagnostic['ecu_make'] = faults_diagnostic['ecu_make'].replace('??MNS', 'CMMNS')
faults_diagnostic['ecu_make'] = faults_diagnostic['ecu_make'].replace('???R', 'PCAR')
faults_diagnostic['ecu_make'] = faults_diagnostic['ecu_make'].replace('??DWS', 'BNDWS')

##### ECU Source

In [21]:
faults_diagnostic['ecu_source'].value_counts()

0     528044
49    514059
11    131122
3      13484
61       626
Name: ecu_source, dtype: int64

Nothing to clean

##### SPN

In [25]:
faults_diagnostic['spn'].value_counts()

111       365489
929       256541
96         90041
829        87788
639        41062
97         26745
596        22571
50353      11773
1569       10927
1761        9981
2863        8233
789         8022
629         8012
1068        7994
791         7799
1231        6992
1067        6947
641         6292
91          6210
3226        5547
3216        5420
37          5183
792         5164
412         5044
790         5011
807         4945
886         4190
1807        4081
627         4043
802         4036
171         4036
611         4026
1059        3952
51923       3950
793         3906
3251        3905
3464        3382
4364        2618
102         2578
630         2460
157         2426
70          2268
5396        2223
1483        2178
5848        2100
3610        2021
1045        1994
907         1962
4096        1877
5444        1800
1209        1736
523531      1718
2623        1700
101         1686
110         1652
3031        1650
1808        1636
934         1613
248         16

Nothing to clean

##### FMI

In [26]:
faults_diagnostic['fmi'].value_counts()

17    326553
9     288893
3     188631
2      82334
18     53602
31     39881
4      39734
0      27577
7      23249
1      20887
15     20739
14     12699
12     12233
5       9683
16      9242
10      7437
8       5741
19      5733
20      4440
11      3847
13      2634
6       1027
23       396
21       131
29         8
22         4
Name: fmi, dtype: int64

Nothing to clean

##### Active

In [27]:
faults_diagnostic['active'].value_counts(normalize=True)

True     0.512454
False    0.487546
Name: active, dtype: float64

Nothing to clean

##### Active Count

In [31]:
faults_diagnostic['active_transition_count'].value_counts()

126    581874
1      305476
127    102512
2       45075
3       13019
4        9658
6        6880
5        6777
0        5781
7        4782
8        4088
9        3750
11       3387
10       3326
12       2713
13       2603
14       2420
15       2358
16       2158
17       2064
18       1914
20       1755
19       1753
21       1590
22       1482
23       1475
24       1459
25       1393
26       1391
28       1277
27       1276
29       1230
30       1164
33       1132
32       1128
31       1074
34       1039
36       1000
39        973
40        972
37        970
35        968
38        965
44        915
43        908
42        906
41        896
45        837
48        832
46        813
47        811
50        800
49        798
55        762
52        747
54        738
51        731
53        728
59        723
58        720
56        689
57        687
63        676
61        671
64        655
70        648
62        644
60        624
66        623
72        618
67        618
68    

Nothing to clean

##### Equipment ID

In [32]:
faults_diagnostic['equipment_id'].value_counts()

1641          17492
1605          16393
1646          15462
1618          14986
1606          14973
1619          14832
1625          14783
1645          14268
1644          13920
1649          13557
1610          13489
1630          13149
1647          13117
1634          13003
1609          12902
1642          12653
1623          11834
1611          11804
1814          10361
1692          10301
1612           9554
1816           8164
1809           8026
1939           7966
1622           7918
1806           7771
1601           7437
1603           7141
1469           7116
1592           7085
1749           7000
1808           6856
1815           6474
1803           6390
1437           6133
309            5991
305            5738
1600           5684
1804           5670
1589           5532
1562           5483
1620           5470
1995           5365
1559           5358
1818           5135
1820           5080
1616           5015
1810           4883
1422           4736
1873           4584


# Per the instructions, we'll need to remove any equipment_id that is greater than 5 digits (Google 'drop columns that meet condition')

In [34]:
faults_diagnostic[faults_diagnostic['equipment_id'].str.len() > 5]

record_id     ess_id     event_timestamp  \
7069          7070    1157485 2015-03-03 09:18:42   
7070          7071    1157507 2015-03-03 09:19:43   
59121        61191    2545755 2015-05-21 08:16:17   
59587        61657    2553312 2015-05-21 13:27:44   
60728        62798    2570947 2015-05-22 10:44:37   
60911        62981    2574542 2015-05-22 13:21:38   
62903        64973    2598094 2015-05-25 07:04:39   
63582        65652    2606983 2015-05-26 04:51:45   
63900        65970    2611699 2015-05-26 09:11:32   
64069        66139    2614629 2015-05-26 10:56:57   
64282        66352    2618007 2015-05-26 13:10:40   
64882        66952    2629063 2015-05-27 04:36:55   
64949        67019    2629859 2015-05-27 05:58:51   
64957        67027    2629898 2015-05-27 06:01:39   
64997        67067    2630384 2015-05-27 06:31:46   
65161        67231    2632939 2015-05-27 08:34:24   
65308        67378    2634787 2015-05-27 09:55:53   
66169        68239    2649511 2015-05-28 02:31:34   
66228        68298    2650389 2015-05-28 04:50:49   
66269        68339    2651009 2015-05-28 05:49:12   
66528        68598    2655567 2015-05-28 09:34:27   
66645        68715    2657649 2015-05-28 10:53:06   
66832        68902    2660825 2015-05-28 12:53:48   
66899        68969    2662078 2015-05-28 13:45:33   
67403        69473    2671238 2015-05-29 02:50:51   
67404        69474    2671239 2015-05-29 02:51:01   
67415        69485    2671462 2015-05-29 03:30:54   
67594        69664    2674721 2015-05-29 07:35:45   
67681        69751    2676151 2015-05-29 08:44:54   
67682        69752    2676154 2015-05-29 08:45:03   
67720        69790    2676592 2015-05-29 09:05:09   
67733        69803    2676844 2015-05-29 09:15:45   
67748        69818    2677194 2015-05-29 09:30:25   
68021        70091    2681027 2015-05-29 12:12:20   
68136        70206    2682877 2015-05-29 13:38:09   
68664        70734    2690836 2015-05-30 01:56:00   
68716        70786    2691488 2015-05-30 04:50:10   
68735        70805    2691963 2015-05-30 06:01:21   
68736        70806    2691964 2015-05-30 06:01:31   
68858        70928    2693739 2015-05-30 08:42:08   
68902        70972    2694502 2015-05-30 09:38:44   
68967        71037    2695900 2015-05-30 11:42:47   
68991        71061    2696263 2015-05-30 12:10:19   
69254        71640    2701156 2015-05-31 01:57:39   
69270        71656    2701494 2015-05-31 04:26:25   
69284        71670    2701834 2015-05-31 06:09:25   
69327        71713    2702378 2015-05-31 07:30:24   
69406        71792    2703686 2015-05-31 10:10:52   
69438        71824    2704256 2015-05-31 11:06:33   
69442        71828    2704312 2015-05-31 11:15:02   
85473        87859    2962286 2015-06-15 13:47:35   
98892       101278    3182462 2015-06-27 09:02:02   
98906       101292    3182663 2015-06-27 09:23:36   
98928       101314    3182922 2015-06-27 09:42:55   
107165      109551    3290501 2010-12-31 23:03:24   
120740      123126    3481454 2015-07-15 09:56:49   
125371      127757    3554005 2011-01-01 01:03:38   
143193      145579    3784898 2015-07-31 07:08:30   
146183      148569    3827314 2015-08-03 10:46:47   
146200      148586    3827615 2015-08-03 11:00:46   
146481      148867    3832916 2015-08-03 12:05:51   
153612      155998    3926046 2015-08-07 15:15:11   
154313      156699    3937403 2015-08-08 11:52:51   
154314      156700    3937404 2015-08-08 11:52:51   
154369      156755    3938250 2015-08-08 13:03:40   
154370      156756    3938251 2015-08-08 13:03:01   
154371      156757    3938268 2015-08-08 13:04:49   
154372      156758    3938270 2015-08-08 13:04:10   
154393      156779    3938563 2015-08-08 13:33:15   
154394      156780    3938564 2015-08-08 13:33:15   
154399      156785    3938603 2015-08-08 13:36:48   
154403      156789    3938674 2015-08-08 13:41:14   
154483      156869    3939858 2015-08-08 15:50:24   
154484      156870    3939860 2015-08-08 15:49:46   
154490      156876    3940024 2015

##### MCT Number

In [37]:
faults_diagnostic['mct_number'].value_counts()

105415080    16503
105420184    15507
105381514    15330
105415457    15119
105416377    15034
105417985    13590
105442858    13187
105420195    13141
105415391    13079
105338710    11834
105420590    11038
105357098    10719
105369518    10430
105420520     9939
105320363     9580
105430420     8590
105420005     8532
105465351     8361
105420580     8111
105434215     8096
105351093     8064
105330008     8019
105304730     8018
105438415     8014
105415630     7889
105364937     7479
105357794     7265
105411041     7190
105357909     6937
105400037     6929
105438416     6879
105355660     6724
105333857     6639
105460307     6529
105432778     6421
105356370     6406
105442799     6200
105435663     6040
105334108     5978
105392933     5872
105410475     5784
105356577     5734
105406655     5728
105338555     5726
105362919     5675
105460271     5670
105410840     5610
105412415     5316
105349500     5165
105465571     5080
105465373     5054
105411109     5009
105427242   

Nothing to clean

##### Latitude and Longitude

In [49]:
faults_diagnostic[faults_diagnostic['latitude'] == 0]

record_id     ess_id     event_timestamp  \
891610      915675   32752046 2017-11-21 11:28:06   
891672      915737   32763318 2017-11-21 13:10:27   
1150008    1207232  106294736 2019-06-24 09:10:10   
1150009    1207233  106294737 2019-06-24 09:10:09   
1150010    1207234  106294738 2019-06-24 09:10:11   
1150011    1207235  106294739 2019-06-24 09:10:12   
1172275    1231439  116418325 2020-01-09 20:50:32   
1172276    1231440  116418326 2020-01-09 20:50:32   

                                         event_description  \
891610          Low (Severity Medium) Engine Coolant Level   
891672          Low (Severity Medium) Engine Coolant Level   
1150008              Low Voltage (Sensor supply voltage 2)   
1150009  Low Voltage (Engine Exhaust Gas Recirculation ...   
1150010                                                NaN   
1150011         Low Current Aftertreatment Fuel Injector 1   
1172275                          High Voltage (Fuel Level)   
1172276              High Voltage (Left Fuel Level Sensor)   

                                    ecu_software_version ecu_serial_number  \
891610   04384413*22057890*031617122339*60701702*G1*BGT*          80012214   
891672   04384413*22057890*031617122339*60701702*G1*BGT*          80012214   
1150008                                          unknown           unknown   
1150009                                          unknown           unknown   
1150010                                              NaN               NaN   
1150011                                          unknown           unknown   
1172275                                              NaN               NaN   
1172276                                              NaN               NaN   

                 ecu_model ecu_make  ecu_source   spn  ...  fuel_temperature  \
891610   6X1u17D1500000000    CMMNS           0   111  ...               NaN   
891672   6X1u17D1500000000    CMMNS           0   111  ...               NaN   
1150008            unknown  unknown           0  3510  ...               NaN   
1150009            unknown  unknown           0    27  ...               NaN   
1150010                NaN      NaN          11  1807  ...               NaN   
1150011            unknown  unknown           0  3556  ...               NaN   
1172275      CECU3B-NAMUX4    PACCR          49    96  ...               NaN   
1172276      CECU3B-NAMUX4    PACCR          49   829  ...               NaN   

         ign_status  intake_manifold_temperature lamp_status  parking_brake  \
891610         True                         66.2        2047           True   
891672          NaN                          NaN        1023            NaN   
1150008        True                        107.6       17407          False   
1150009        True                        105.8       17407          False   
1150010        True                        107.6       63487          False   
1150011        True                        107.6       17407          False   
1172275        True                         84.2        1279           True   
1172276        True                         84.2        1279           True   

         service_distance       speed switched_battery_voltage  throttle  \
891610                NaN           0                       13       100   
891672                NaN         NaN                      NaN       NaN   
1150008               NaN   0.3301035                      NaN       100   
1150009               NaN  0.01941785                      NaN       100   
1150010               NaN   0.9417657                      NaN       100   
1150011               NaN    3.893279                      NaN       100   
1172275               NaN           0                      NaN       100   
1172276               NaN           0                      NaN       100   

        turbo_boost_pressure  
891610                     0  
891672                   NaN  
1150008                    0  
1150009                    

8 rows contain a latitude of 0.0

In [52]:
faults_diagnostic[faults_diagnostic['longitude'] == 0]

record_id     ess_id     event_timestamp  \
891610      915675   32752046 2017-11-21 11:28:06   
891672      915737   32763318 2017-11-21 13:10:27   
1150008    1207232  106294736 2019-06-24 09:10:10   
1150009    1207233  106294737 2019-06-24 09:10:09   
1150010    1207234  106294738 2019-06-24 09:10:11   
1150011    1207235  106294739 2019-06-24 09:10:12   
1172275    1231439  116418325 2020-01-09 20:50:32   
1172276    1231440  116418326 2020-01-09 20:50:32   

                                         event_description  \
891610          Low (Severity Medium) Engine Coolant Level   
891672          Low (Severity Medium) Engine Coolant Level   
1150008              Low Voltage (Sensor supply voltage 2)   
1150009  Low Voltage (Engine Exhaust Gas Recirculation ...   
1150010                                                NaN   
1150011         Low Current Aftertreatment Fuel Injector 1   
1172275                          High Voltage (Fuel Level)   
1172276              High Voltage (Left Fuel Level Sensor)   

                                    ecu_software_version ecu_serial_number  \
891610   04384413*22057890*031617122339*60701702*G1*BGT*          80012214   
891672   04384413*22057890*031617122339*60701702*G1*BGT*          80012214   
1150008                                          unknown           unknown   
1150009                                          unknown           unknown   
1150010                                              NaN               NaN   
1150011                                          unknown           unknown   
1172275                                              NaN               NaN   
1172276                                              NaN               NaN   

                 ecu_model ecu_make  ecu_source   spn  ...  fuel_temperature  \
891610   6X1u17D1500000000    CMMNS           0   111  ...               NaN   
891672   6X1u17D1500000000    CMMNS           0   111  ...               NaN   
1150008            unknown  unknown           0  3510  ...               NaN   
1150009            unknown  unknown           0    27  ...               NaN   
1150010                NaN      NaN          11  1807  ...               NaN   
1150011            unknown  unknown           0  3556  ...               NaN   
1172275      CECU3B-NAMUX4    PACCR          49    96  ...               NaN   
1172276      CECU3B-NAMUX4    PACCR          49   829  ...               NaN   

         ign_status  intake_manifold_temperature lamp_status  parking_brake  \
891610         True                         66.2        2047           True   
891672          NaN                          NaN        1023            NaN   
1150008        True                        107.6       17407          False   
1150009        True                        105.8       17407          False   
1150010        True                        107.6       63487          False   
1150011        True                        107.6       17407          False   
1172275        True                         84.2        1279           True   
1172276        True                         84.2        1279           True   

         service_distance       speed switched_battery_voltage  throttle  \
891610                NaN           0                       13       100   
891672                NaN         NaN                      NaN       NaN   
1150008               NaN   0.3301035                      NaN       100   
1150009               NaN  0.01941785                      NaN       100   
1150010               NaN   0.9417657                      NaN       100   
1150011               NaN    3.893279                      NaN       100   
1172275               NaN           0                      NaN       100   
1172276               NaN           0                      NaN       100   

        turbo_boost_pressure  
891610                     0  
891672                   NaN  
1150008                    0  
1150009                    

The same 8 rows contain a longitude of 0.0

## Potentially remove records at (0.0, 0.0) Lat, Long AND need to filter out service stations using Patti's code

##### Location Timestamp

In [62]:
faults_diagnostic['location_timestamp'].dt.year.value_counts()

2016    332403
2015    325826
2017    254923
2018    144578
2019    112204
2020     17198
2000       192
2011         8
1969         2
2014         1
Name: location_timestamp, dtype: int64

We'll need to investigate the records pre-2014

In [63]:
faults_diagnostic[faults_diagnostic['location_timestamp'].dt.year == 1969]

record_id    ess_id     event_timestamp  \
891610     915675  32752046 2017-11-21 11:28:06   
891672     915737  32763318 2017-11-21 13:10:27   

                                 event_description  \
891610  Low (Severity Medium) Engine Coolant Level   
891672  Low (Severity Medium) Engine Coolant Level   

                                   ecu_software_version ecu_serial_number  \
891610  04384413*22057890*031617122339*60701702*G1*BGT*          80012214   
891672  04384413*22057890*031617122339*60701702*G1*BGT*          80012214   

                ecu_model ecu_make  ecu_source  spn  ...  fuel_temperature  \
891610  6X1u17D1500000000    CMMNS           0  111  ...               NaN   
891672  6X1u17D1500000000    CMMNS           0  111  ...               NaN   

        ign_status  intake_manifold_temperature lamp_status  parking_brake  \
891610        True                         66.2        2047           True   
891672         NaN                          NaN        1023            NaN   

        service_distance  speed switched_battery_voltage  throttle  \
891610               NaN      0                       13       100   
891672               NaN    NaN                      NaN       NaN   

       turbo_boost_pressure  
891610                    0  
891672                  NaN  

[2 rows x 43 columns]

Is there a way to compare location_timestamp to event_timestamp? More importantly, is this worth doing?

In [64]:
faults_diagnostic[faults_diagnostic['location_timestamp'].dt.year == 2000]

record_id     ess_id     event_timestamp  \
1154193    1211417  108604425 2000-03-18 19:14:10   
1154194    1211418  108604426 2000-03-18 19:14:10   
1154195    1211419  108604487 2000-03-18 19:20:47   
1154196    1211420  108604488 2000-03-18 19:20:47   
1154198    1211422  108608408 2000-03-19 02:59:58   
1154199    1211423  108608954 2000-03-19 03:58:23   
1154208    1211432  108615304 2000-03-19 07:32:53   
1154209    1211433  108615321 2000-03-19 07:34:31   
1154211    1211435  108620729 2000-03-19 08:40:03   
1154212    1211436  108620730 2000-03-19 08:40:03   
1154215    1211439  108622089 2000-03-19 08:58:27   
1154216    1211440  108622090 2000-03-19 08:58:27   
1154219    1211443  108622593 2000-03-19 09:03:22   
1154220    1211444  108622594 2000-03-19 09:03:22   
1154223    1211447  108630527 2000-03-19 10:35:14   
1154224    1211448  108630528 2000-03-19 10:35:14   
1154225    1211449  108631659 2000-03-19 10:51:28   
1154228    1211452  108632613 2000-03-19 11:11:02   
1154243    1211467  108634615 2000-03-19 11:42:06   
1154244    1211468  108634616 2000-03-19 11:42:06   
1154245    1211469  108635168 2000-03-19 11:50:17   
1154246    1211470  108635169 2000-03-19 11:50:17   
1154247    1211471  108635373 2000-03-19 11:55:06   
1154248    1211472  108635374 2000-03-19 11:55:06   
1154249    1211473  108636257 2000-03-19 12:08:22   
1154251    1211475  108638110 2000-03-19 12:34:51   
1154252    1211476  108638111 2000-03-19 12:34:51   
1154253    1211477  108638380 2000-03-19 12:38:20   
1154254    1211478  108638381 2000-03-19 12:38:20   
1154255    1211479  108639463 2000-03-19 12:55:01   
1154256    1211480  108639464 2000-03-19 12:55:01   
1154257    1211481  108639840 2000-03-19 13:02:36   
1154258    1211482  108640040 2000-03-19 13:06:49   
1154259    1211483  108640041 2000-03-19 13:06:49   
1154260    1211484  108642452 2000-03-19 13:41:24   
1154261    1211485  108642453 2000-03-19 13:41:24   
1154263    1211487  108644439 2000-03-19 14:02:34   
1154264    1211488  108645372 2000-03-19 14:07:55   
1154265    1211489  108645850 2000-03-19 14:11:59   
1154266    1211490  108646591 2000-03-19 14:17:26   
1154271    1211495  108651978 2000-03-19 15:12:24   
1154272    1211496  108651979 2000-03-19 15:12:24   
1154275    1211499  108653960 2000-03-19 15:35:59   
1154276    1211500  108653961 2000-03-19 15:35:59   
1154277    1211501  108654236 2000-03-19 15:37:49   
1154278    1211502  108654338 2000-03-19 15:39:46   
1154279    1211503  108654582 2000-03-19 15:42:29   
1154280    1211504  108654583 2000-03-19 15:42:30   
1154281    1211505  108655772 2000-03-19 16:05:58   
1154282    1211506  108655773 2000-03-19 16:05:58   
1154283    1211507  108655839 2000-03-19 16:06:32   
1154284    1211508  108656295 2000-03-19 16:13:43   
1154285    1211509  108656621 2000-03-19 16:20:31   
1154286    1211510  108656622 2000-03-19 16:20:31   
1154287    1211511  108656781 2000-03-19 16:25:25   
1154288    1211512  108656844 2000-03-19 16:27:13   
1154293    1211517  108659676 2000-03-19 17:06:22   
1154296    1211520  108659778 2000-03-19 17:08:54   
1154297    1211521  108661657 2000-03-19 17:28:04   
1154298    1211522  108661658 2000-03-19 17:27:44   
1154299    1211523  108661659 2000-03-19 17:27:44   
1154300    1211524  108661660 2000-03-19 17:27:58   
1154301    1211525  108661886 2000-03-19 17:55:53   
1154302    1211526  108662038 2000-03-19 17:59:01   
1154303    1211527  108662262 2000-03-19 18:09:55   
1154304    1211528  108662312 2000-03-19 18:12:16   
1154305    1211529  108662313 2000-03-19 18:12:16   
1154306    1211530  108662645 2000-03-19 18:02:53   
1154307    1211531  108662646 2000-03-19 18:02:53   
1154308    1211532  108662647 2000-03-19 18:02:53   
1154309    1211533  108663626 2000-03-19 18:56:09   
1154310    1211534  108663627 2000-03-19 18:56:09   
1154311    1211535  108664021 2000-03-19 19:13:54   
1154312    1211536  108664067 2000-03-19 19:17:46   
1154313    1211537  108665697 2000

Interesting...the 2000 records appear to have the event_timestamps and location_timestamps in the same year

In [65]:
faults_diagnostic[faults_diagnostic['location_timestamp'].dt.year == 2011]

record_id     ess_id     event_timestamp  \
1154812    1212036  108848937 2011-01-02 03:17:37   
1155217    1212441  109079376 2011-01-01 05:10:23   
1155218    1212442  109079377 2011-01-01 05:09:43   
1155219    1212443  109079378 2011-01-01 05:11:26   
1155230    1212454  109079376 2011-01-01 05:10:23   
1155231    1212455  109079377 2011-01-01 05:09:43   
1155232    1212456  109079378 2011-01-01 05:11:26   
1171320    1230484  115919584 2011-01-01 00:10:32   

                                         event_description  \
1154812             Low (Severity Low) Catalyst Tank Level   
1155217  Special Instructions Transmission Clutch Actuator   
1155218  Low (Severity Medium) Transmission Air Tank Pr...   
1155219  Low (Severity Medium) Transmission Air Tank Pr...   
1155230  Special Instructions Transmission Clutch Actuator   
1155231  Low (Severity Medium) Transmission Air Tank Pr...   
1155232  Low (Severity Medium) Transmission Air Tank Pr...   
1171320  Low (Severity High) Transmission Air Tank Pres...   

                                      ecu_software_version ecu_serial_number  \
1154812    04384413*22059242*090617144354*60701715*G1*BGT*          80015667   
1155217  5516018*202.56.0*5516502*E003.e003*5539540*25....          Z0018064   
1155218  5516018*202.56.0*5516502*E003.e003*5539540*25....          Z0018064   
1155219  5516018*202.56.0*5516502*E003.e003*5539540*25....          Z0018064   
1155230  5516018*202.56.0*5516502*E003.e003*5539540*25....          Z0018064   
1155231  5516018*202.56.0*5516502*E003.e003*5539540*25....          Z0018064   
1155232  5516018*202.56.0*5516502*E003.e003*5539540*25....          Z0018064   
1171320  5516014*202.35.0*5516502*E003.e003*5539478*25....          Z0047881   

                 ecu_model ecu_make  ecu_source   spn  ...  fuel_temperature  \
1154812  6X1u17D1500000000    CMMNS           0  1761  ...               NaN   
1155217        EEO-xxF112C    EATON           3   788  ...               NaN   
1155218        EEO-xxF112C    EATON           3    37  ...               NaN   
1155219        EEO-xxF112C    EATON           3    37  ...               NaN   
1155230        EEO-xxF112C    EATON           3   788  ...               NaN   
1155231        EEO-xxF112C    EATON           3    37  ...               NaN   
1155232        EEO-xxF112C    EATON           3    37  ...               NaN   
1171320        EEO-xxF112C    EATON           3    37  ...               NaN   

         ign_status  intake_manifold_temperature lamp_status  parking_brake  \
1154812        True                        127.4        1023           True   
1155217         NaN                          NaN       50175            NaN   
1155218        True                        105.8       50175           True   
1155219         NaN                          NaN       50175            NaN   
1155230         NaN                          NaN       50175            NaN   
1155231        True                        105.8       50175           True   
1155232         NaN                          NaN       50175            NaN   
1171320        True                        125.6       50175          False   

         service_distance     speed switched_battery_voltage  throttle  \
1154812               NaN         0                      NaN       100   
1155217               NaN       NaN                      NaN       NaN   
1155218               NaN         0                      NaN       100   
1155219               NaN       NaN                      NaN       NaN   
1155230               NaN       NaN                      NaN       NaN   
1155231               NaN         0                      NaN       100   
1155232               NaN       NaN                      NaN       NaN   
1171320               NaN  3.116565                      NaN       100   

        turbo_boost_pressure  
1154812                 0.29  
1155217                  NaN  
1155218                 0.29  
1155219                  Na

In [66]:
faults_diagnostic[faults_diagnostic['location_timestamp'].dt.year == 2014]

record_id   ess_id     event_timestamp  \
27724      28607  1994354 2015-04-21 03:31:18   

                                       event_description ecu_software_version  \
27724  Abnormal Rate of Change Aftertreatment 1 Outle...              unknown   

      ecu_serial_number ecu_model ecu_make  ecu_source   spn  ...  \
27724           unknown   unknown  unknown           0  3226  ...   

       fuel_temperature  ign_status  intake_manifold_temperature lamp_status  \
27724               NaN        True                          NaN       17407   

       parking_brake  service_distance  speed switched_battery_voltage  \
27724            NaN               NaN    NaN                      NaN   

       throttle turbo_boost_pressure  
27724       NaN                  NaN  

[1 rows x 43 columns]

Given the discrepancies, it may make sense to use only one timestamp column

##### Fault ID

'fault_id' was used to join the datasets and is redundant with 'record_id'. We'll drop it now

In [69]:
faults_diagnostic = faults_diagnostic.drop(columns=['fault_id'])

##### Accelerator Pedal

In [73]:
faults_diagnostic['accelerator_pedal'].value_counts()

0           277162
100          54097
99.6          2845
0.4           1945
27.2          1911
27.6          1867
28.4          1863
28            1824
28.8          1816
25.2          1799
26.8          1798
26.4          1795
29.6          1789
25.6          1773
26            1757
24.4          1724
30.8          1717
29.2          1717
31.6          1688
30.4          1680
32            1667
32.8          1652
22.8          1641
31.2          1632
23.6          1618
33.2          1617
33.6          1603
23.2          1596
24            1589
30            1581
32.4          1581
24.8          1571
34            1518
22            1505
21.6          1502
0.8           1499
34.4          1494
22.4          1476
35.2          1466
21.2          1420
20.8          1393
20.4          1370
36.4          1354
36.8          1340
35.6          1329
99.2          1326
36            1310
34.8          1282
37.6          1281
37.2          1273
19.6          1252
38.4          1252
19.2        

Several values have commas—this is consistent across the diagnostic data, so we'll clean those all up at once

##### Barometric Pressure

In [75]:
faults_diagnostic['barometric_pressure'].value_counts()

14.355      85896
14.4275     82204
14.2825     76928
14.5        56948
14.21       56774
14.5725     40218
14.1375     37674
14.645      32327
14.065      21697
14.7175     20403
13.9925     11526
14.79        7784
13.92        7230
13.775       6661
13.8475      6560
13.7025      6529
13.63        5858
13.5575      4354
3.5525       3326
13.485       3120
14.8625      2420
13.4125      2118
3.625        1448
13.34        1130
3.48          822
14.935        685
13.2675       599
12.2525       311
3.4075        280
13.195        237
15.0075       182
7.25          182
13.1225       155
3.6975        121
3.335         118
13.05         109
12.9775       104
12.615         87
12.8325        70
12.6875        60
12.905         51
11.6725        43
12.76          43
12.5425        40
12.325         39
12.3975        34
11.9625        33
12.18          33
11.455         31
11.6           31
12.035         30
11.745         27
11.5275        26
12.47          26
11.89          24
15.08     

Commas to be fixed

##### Cruise Control Active

In [77]:
faults_diagnostic['cruise_control_active'].value_counts(normalize=True)

False    0.911756
True     0.088244
Name: cruise_control_active, dtype: float64

In [78]:
faults_diagnostic['cruise_control_set_speed'].value_counts()

66.48672    278248
64.6226     130757
0            34698
65.24397     10955
65.86535      9688
64.00124      9305
59.65163      8075
63.37986      6705
61.51575      6642
60.89438      6638
60.27301      5859
55.30204      5712
59.03026      5303
62.75849      5230
56.54478      4817
57.78752      4581
57.16615      4322
62.13712      4264
54.68066      4243
55.92341      4235
58.40889      4225
67.10809      4060
42.25324      2271
54.05929      2213
53.43792       935
68.35083       902
52.81655       748
50.33107       742
68.97221       669
51.57381       626
49.70969       537
52.19518       516
45.3601        465
44.73873       464
47.84558       451
45.98147       440
46.60284       410
41.63187       410
44.11736       390
50.95244       374
47.22421       345
67.72946       341
49.08833       304
70.83632       275
48.46695       242
27.9617        199
70.21494       198
31.68993       191
40.38913       190
43.49598       160
29.82582       150
29.20445       139
34.79679    

There are 34,698 records that have cruise control set to 0 mph. Interesting

##### Distance (Lifetime To Date)

In [87]:
faults_diagnostic['distance_ltd']

0             423178.7
1                  NaN
2                  NaN
3                  NaN
4                  NaN
              ...     
1187330            NaN
1187331       423937.9
1187332       465925.4
1187333    28606.65625
1187334            NaN
Name: distance_ltd, Length: 1187335, dtype: object

We'll need to fix commas before going further

In [ ]:
comma_columns = ['accelerator_pedal',
                'barometric_pressure',
                'distance_ltd'
                ]

In [70]:
faults_diagnostic.columns

Index(['record_id', 'ess_id', 'event_timestamp', 'event_description',
       'ecu_software_version', 'ecu_serial_number', 'ecu_model', 'ecu_make',
       'ecu_source', 'spn', 'fmi', 'active', 'active_transition_count',
       'equipment_id', 'mct_number', 'latitude', 'longitude',
       'location_timestamp', 'accelerator_pedal', 'barometric_pressure',
       'cruise_control_active', 'cruise_control_set_speed', 'distance_ltd',
       'engine_coolant_temperature', 'engine_load', 'engine_oil_pressure',
       'engine_oil_temperature', 'engine_rpm', 'engine_time_ltd', 'fuel_level',
       'fuel_ltd', 'fuel_rate', 'fuel_temperature', 'ign_status',
       'intake_manifold_temperature', 'lamp_status', 'parking_brake',
       'service_distance', 'speed', 'switched_battery_voltage', 'throttle',
       'turbo_boost_pressure'],
      dtype='object')